# Explore Curation Events

In [1]:
# standard imports
import pandas as pd
import json
import requests
import matplotlib.pyplot as plt
import numpy as np
from eth_utils import keccak
#from web3 import Web3

In [4]:
# function used to query each type of event from The Graph
def query_theGraph(raw_query, field_name, url, trans_type, verbose=False):

    query_parts =raw_query.split(')')
    paginator = ", where: {}" 
    n = 0
    records = []
    while n < 1000:
        if (n == 0):
            # order by blockNumber to get all events, as deafult ordering is by id
            query = 'query '+query_parts[0] + 'orderBy:blockNumber, where:{blockNumber_gt: 0, type:' + trans_type +'})' + query_parts[1]
        else:
            query = 'query '+query_parts[0]+ 'orderBy:blockNumber, where: {blockNumber_gt: ' + str(indexer) + ', type:' + trans_type +'})'+query_parts[1]

        if verbose:
            print(query)

        r = requests.post(url, json = {'query':query})

        try:
            d = json.loads(r.content)['data'][field_name]
        except:
            print(r.content)
            errors = json.loads(r.content)['errors']
            print(errors)
            for e in errors:
                print(e['message'])

        #print(f'results {len(d)}')
        records.extend(d)
        #print(f'total {len(records)}')
        try:
            indexer = d[-1]['blockNumber']
        except:
            print('noblock')
        
        n += 1
        if len(d) < 99:
            break
        
    return pd.DataFrame(records)

In [5]:
#get allocationCreated event
url = 'https://api.thegraph.com/subgraphs/name/graphprotocol/graph-network-mainnet'

minted_query = '''query{
  signalTransactions() {
    id
    blockNumber
    signer{
      curator
      {
        id
      }
    }
    signal
    tokens
    type
    subgraphDeployment{
     id
    } 
  }  
}
'''

field_name = 'signalTransactions'
trans_type = 'MintSignal'

curation_mint_df = query_theGraph(minted_query, field_name, url, trans_type, False)

In [6]:
#alloc_created_df.to_csv('allocationCreateds.csv', index = False, header = True)
curation_mint_df.head()

id  blockNumber  \
0  0x4c1060853752b5221b1e27c2264034d0bd5fd86c5267...     11474121   
1  0xea7dbe2f6164530a53ac8cf9d99b46993f44d8ca8258...     11476852   
2  0xfbdb37e510284ebbeb45fbfdf28191219faf84bc31bf...     11476875   
3  0xfbda17a348fb979ad36e27445d656b23458a938fadd2...     11476931   
4  0x395da0c992967e085a68fd69825c8f629486ef10d48b...     11531681   

                                              signer                 signal  \
0  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...  279284800875378823397   
1  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...     627949250367270370   
2  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...  125503147008134479971   
3  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...   89477475325111327822   
4  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...       1568268903568881   

                    tokens        type  \
0  78000000000000000000000  MintSignal   
1    351147682958369832716  MintSignal   
2  86010901965910864972811  MintSignal   
3  80557400454965249175744  MintSignal   
4       975000000000000000  MintSignal   

                                  subgraphDeployment  
0  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...  
1  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...  
2  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...  
3  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...  
4  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...

In [7]:
curation_mint_df['signer'] = [i['curator']['id'] for i in curation_mint_df['signer']]
curation_mint_df['subgraphDeployment']  = [i['id'] for i in curation_mint_df['subgraphDeployment']]
curation_mint_df.head()

id  blockNumber  \
0  0x4c1060853752b5221b1e27c2264034d0bd5fd86c5267...     11474121   
1  0xea7dbe2f6164530a53ac8cf9d99b46993f44d8ca8258...     11476852   
2  0xfbdb37e510284ebbeb45fbfdf28191219faf84bc31bf...     11476875   
3  0xfbda17a348fb979ad36e27445d656b23458a938fadd2...     11476931   
4  0x395da0c992967e085a68fd69825c8f629486ef10d48b...     11531681   

                                       signer                 signal  \
0  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825  279284800875378823397   
1  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825     627949250367270370   
2  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825  125503147008134479971   
3  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825   89477475325111327822   
4  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825       1568268903568881   

                    tokens        type  \
0  78000000000000000000000  MintSignal   
1    351147682958369832716  MintSignal   
2  86010901965910864972811  MintSignal   
3  80557400454965249175744  MintSignal   
4       975000000000000000  MintSignal   

                                  subgraphDeployment  
0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
1  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
2  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
3  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
4  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...

In [30]:
len(curation_mint_df)

7607

In [10]:
#get allocationCreated event
url = 'https://api.thegraph.com/subgraphs/name/graphprotocol/graph-network-mainnet'

created_query = '''query{
  signalTransactions() {
    id
    blockNumber
    signer{
      curator
      {
        id
      }
    }
    signal
    tokens
    type
    subgraphDeployment{
     id
    } 
  }  
}
'''

field_name = 'signalTransactions'
trans_type = 'BurnSignal'

curation_burned_df = query_theGraph(created_query, field_name, url, trans_type, False)

In [11]:
curation_burned_df.head()

id  blockNumber  \
0  0xf5fd904385312b521779beb91a757a403132ebf7bbf7...     11486499   
1  0x7b0d39ca37ba86fd5e6ecc4433513ffba4b853a90bd2...     11491383   
2  0xe46b8054c269f1c5811dc5cdd0d4564bb92f370477df...     11491393   
3  0x620c0af5345f21ec87c9b73864d3709d735fb7aac155...     11531871   
4  0x10afff8568c6e870a7b596787cb284e43842892e3a74...     12318426   

                                              signer                signal  \
0  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...  89477475325111327822   
1  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...                    95   
2  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...  95000000000000000000   
3  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...      1568268903568881   
4  {'curator': {'id': '0xadca0dd4729c8ba3acf3e99f...   1000000000000000000   

                    tokens        type  \
0  80557400454965249175496  BurnSignal   
1                    77029  BurnSignal   
2  68004020455437308993046  BurnSignal   
3       975006929934390676  BurnSignal   
4    545931348525571351761  BurnSignal   

                                  subgraphDeployment  
0  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...  
1  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...  
2  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...  
3  {'id': '0x31edcacc9a53bc8ab4be2eeb0d873409da4c...  
4  {'id': '0xbbde25a2c85f55b53b7698b9476610c3d120...

In [12]:
curation_burned_df['signer'] = [i['curator']['id'] for i in curation_burned_df['signer']]
curation_burned_df['subgraphDeployment']  = [i['id'] for i in curation_burned_df['subgraphDeployment']]
curation_burned_df.head()

id  blockNumber  \
0  0xf5fd904385312b521779beb91a757a403132ebf7bbf7...     11486499   
1  0x7b0d39ca37ba86fd5e6ecc4433513ffba4b853a90bd2...     11491383   
2  0xe46b8054c269f1c5811dc5cdd0d4564bb92f370477df...     11491393   
3  0x620c0af5345f21ec87c9b73864d3709d735fb7aac155...     11531871   
4  0x10afff8568c6e870a7b596787cb284e43842892e3a74...     12318426   

                                       signer                signal  \
0  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825  89477475325111327822   
1  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825                    95   
2  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825  95000000000000000000   
3  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825      1568268903568881   
4  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825   1000000000000000000   

                    tokens        type  \
0  80557400454965249175496  BurnSignal   
1                    77029  BurnSignal   
2  68004020455437308993046  BurnSignal   
3       975006929934390676  BurnSignal   
4    545931348525571351761  BurnSignal   

                                  subgraphDeployment  
0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
1  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
2  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
3  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
4  0xbbde25a2c85f55b53b7698b9476610c3d1202d88870e...

In [ ]:
# #get allocationCreated event
# url = 'https://api.thegraph.com/subgraphs/name/fordn/graph-network-events'

# created_query = '''query{
#   grtwithdrawns() {
#     id
#     blockNumber
#     blockTime
#     eventTime
#     graphAccount
#     subgraphNumber
#     nameCurator
#     nSignalBurnt
#     withdrawnGRT
#   }  
# }
# '''

# field_name = 'grtwithdrawns'

# curation_withdraw_df = query_theGraph(created_query, field_name, url, False)

In [ ]:
# #save allocationCreated data
# curation_withdraw_df['type'] = 'curationWithdraw'
# #alloc_created_df.to_csv('allocationCreateds.csv', index = False, header = True)
# curation_withdraw_df.head()

In [29]:
indexer_df = pd.read_csv('../another_indexer/single_indexer/singleIndexer.csv', low_memory = False)
indexer_df.head()
len(indexer_df)

1529

In [18]:
subgraph_df = indexer_df[indexer_df['subgraphDeploymentID'].isna() != 1]

In [19]:
unique_subgraphs = subgraph_df['subgraphDeploymentID'].unique()

In [21]:
unique_subgraphs[1]

'0x500a8e47cbdeca7386448ae9e7d52578871b9942ebbef4892469da293bb661f9'

In [32]:
indexer_curation_df = curation_mint_df[curation_mint_df['subgraphDeployment'].isin(unique_subgraphs)].append(curation_burned_df[curation_burned_df['subgraphDeployment'].isin(unique_subgraphs)])

In [33]:
indexer_curation_df.head()

id  blockNumber  \
0  0x4c1060853752b5221b1e27c2264034d0bd5fd86c5267...     11474121   
1  0xea7dbe2f6164530a53ac8cf9d99b46993f44d8ca8258...     11476852   
2  0xfbdb37e510284ebbeb45fbfdf28191219faf84bc31bf...     11476875   
3  0xfbda17a348fb979ad36e27445d656b23458a938fadd2...     11476931   
4  0x395da0c992967e085a68fd69825c8f629486ef10d48b...     11531681   

                                       signer                 signal  \
0  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825  279284800875378823397   
1  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825     627949250367270370   
2  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825  125503147008134479971   
3  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825   89477475325111327822   
4  0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825       1568268903568881   

                    tokens        type  \
0  78000000000000000000000  MintSignal   
1    351147682958369832716  MintSignal   
2  86010901965910864972811  MintSignal   
3  80557400454965249175744  MintSignal   
4       975000000000000000  MintSignal   

                                  subgraphDeployment  
0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
1  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
2  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
3  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
4  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...

In [34]:
len(indexer_curation_df)

1766

In [35]:
single_indexer_df = indexer_df.append(indexer_curation_df)
single_indexer_df.sort_values(by='blockNumber')
single_indexer_df.reset_index(inplace = True)
single_indexer_df.head()

index allocationID  blockNumber  epoch  \
0      0          NaN     11474009    NaN   
1      1          NaN     11474009    NaN   
2      2          NaN     11474307    NaN   
3      3          NaN     11474332    NaN   
4      4          NaN     11474426    NaN   

                                                  id  \
0  0xcb621a8a549e4e3c616a7a1e27dc92b28722c90ac37f...   
1  0xcb621a8a549e4e3c616a7a1e27dc92b28722c90ac37f...   
2  0x938641c2dbfd4562c7ab8c60ca98f11394d161ead6b9...   
3  0x67278b0af539dff48945b3a430ada90de00526aed433...   
4  0x19cf8bd30df43cc8518c16bfce7297c32495bbc3c4c1...   

                                      indexer  logIndex subgraphDeploymentID  \
0  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e     121.0                  NaN   
1  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e     122.0                  NaN   
2  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e      17.0                  NaN   
3  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e      38.0                  NaN   
4  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e     162.0                  NaN   

                      tokens                          type  ...  \
0                        NaN  delegationParametersUpdateds  ...   
1  9615385000000000000000000               stakeDepositeds  ...   
2   165851137200000000000000               stakeDelegateds  ...   
3   251819644650000000000000               stakeDelegateds  ...   
4                        NaN  delegationParametersUpdateds  ...   

                     shares eventTime until indexingRewardCut queryFeeCut  \
0                       NaN       NaN   NaN         1000000.0   1000000.0   
1                       NaN       NaN   NaN               NaN         NaN   
2  165851137200000000000000       NaN   NaN               NaN         NaN   
3  251819644650000000000000       NaN   NaN               NaN         NaN   
4                       NaN       NaN   NaN           90000.0     80000.0   

  delegationFees amount  signer  signal  subgraphDeployment  
0            NaN    NaN     NaN     NaN                 NaN  
1            NaN    NaN     NaN     NaN                 NaN  
2            NaN    NaN     NaN     NaN                 NaN  
3            NaN    NaN     NaN     NaN                 NaN  
4            NaN    NaN     NaN     NaN                 NaN  

[5 rows x 26 columns]

In [36]:
len(single_indexer_df)

3295

In [38]:
# save all events for the indexer
single_indexer_df.to_csv('../another_indexer/single_indexer/singleIndexer.csv', index = False, header = True)

In [25]:
indexer_curation_df = pd.DataFrame()
for i, j in curation_mint_df.iterrows():
    if j['subgraphDeployment'] in unique_subgraphs:
        indexer_curation_df.append(curation_mint_df.iloc[i])
    print(curation_mint_df.iloc[i])
indexer_curation_df.head()

id                    0x4c1060853752b5221b1e27c2264034d0bd5fd86c5267...
blockNumber                                                    11474121
signer                       0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825
signal                                            279284800875378823397
tokens                                          78000000000000000000000
type                                                         MintSignal
subgraphDeployment    0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...
Name: 0, dtype: object
id                    0xea7dbe2f6164530a53ac8cf9d99b46993f44d8ca8258...
blockNumber                                                    11476852
signer                       0xadca0dd4729c8ba3acf3e99f3a9f471ef37b6825
signal                                               627949250367270370
tokens                                            351147682958369832716
type                                                         MintSignal
subgraphDeployment    0x31edcacc9a53bc8ab

Empty DataFrame
Columns: []
Index: []

# GNS Exploration

In [47]:
#get allocationCreated event
url = 'https://api.thegraph.com/subgraphs/name/graphprotocol/graph-network-mainnet'

name_mint_query = '''query{
  nameSignalTransactions(){
    id
    blockNumber
    signer{
      curator{
        id
      }
    }
    type
    nameSignal
    versionSignal
    tokens
    subgraph{
      id
      currentVersion
      {
        version
        subgraphDeployment {
          id
        }
      }
      displayName
    }
  }
}
'''

field_name = 'nameSignalTransactions'
trans_type = 'MintNSignal'

name_mint_df = query_theGraph(name_mint_query, field_name, url, trans_type, False)

In [48]:
name_mint_df.head()

id  blockNumber  \
0  0x4c1060853752b5221b1e27c2264034d0bd5fd86c5267...     11474121   
1  0xea7dbe2f6164530a53ac8cf9d99b46993f44d8ca8258...     11476852   
2  0xfbdb37e510284ebbeb45fbfdf28191219faf84bc31bf...     11476875   
3  0xfbda17a348fb979ad36e27445d656b23458a938fadd2...     11476931   
4  0x395da0c992967e085a68fd69825c8f629486ef10d48b...     11531681   

                                              signer         type  \
0  {'curator': {'id': '0x93606b27cb5e4c780883ec4f...  MintNSignal   
1  {'curator': {'id': '0x0f3cf18b37c55f5a319d6cae...  MintNSignal   
2  {'curator': {'id': '0x0f3cf18b37c55f5a319d6cae...  MintNSignal   
3  {'curator': {'id': '0xb6916933aa0bac4b6d092607...  MintNSignal   
4  {'curator': {'id': '0x849ed8601451dcac8012425c...  MintNSignal   

              nameSignal          versionSignal                   tokens  \
0  279284800875378823397  279284800875378823397  80000000000000000000000   
1     627949250367270370     627949250367270370    360151469700892136118   
2  125503147008134479971  125503147008134479971  88216309708626528177242   
3   89477475325111327822   89477475325111327822  82622974825605383769993   
4       1568268903568881       1568268903568881      1000000000000000000   

                                            subgraph  
0  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  
1  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  
2  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  
3  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  
4  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...

In [49]:
name_mint_df['curatorId'] = [i['curator']['id'] for i in name_mint_df['signer']]
name_mint_df['subgraphId'] = [i['id'] for i in name_mint_df['subgraph']]
name_mint_df['subgraphDeploymentID'] = [i['currentVersion']['subgraphDeployment']['id'] for i in name_mint_df['subgraph']]
name_mint_df['subgraphversion'] = [i['currentVersion']['version'] for i in name_mint_df['subgraph']]
name_mint_df['subgraphname'] = [i['displayName'] for i in name_mint_df['subgraph']]
name_mint_df.drop(['signer','subgraph'], axis = 1, inplace = True)
name_mint_df.head()

id  blockNumber  \
0  0x4c1060853752b5221b1e27c2264034d0bd5fd86c5267...     11474121   
1  0xea7dbe2f6164530a53ac8cf9d99b46993f44d8ca8258...     11476852   
2  0xfbdb37e510284ebbeb45fbfdf28191219faf84bc31bf...     11476875   
3  0xfbda17a348fb979ad36e27445d656b23458a938fadd2...     11476931   
4  0x395da0c992967e085a68fd69825c8f629486ef10d48b...     11531681   

          type             nameSignal          versionSignal  \
0  MintNSignal  279284800875378823397  279284800875378823397   
1  MintNSignal     627949250367270370     627949250367270370   
2  MintNSignal  125503147008134479971  125503147008134479971   
3  MintNSignal   89477475325111327822   89477475325111327822   
4  MintNSignal       1568268903568881       1568268903568881   

                    tokens                                   curatorId  \
0  80000000000000000000000  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd   
1    360151469700892136118  0x0f3cf18b37c55f5a319d6cae8d8ba114cb094af0   
2  88216309708626528177242  0x0f3cf18b37c55f5a319d6cae8d8ba114cb094af0   
3  82622974825605383769993  0xb6916933aa0bac4b6d09260719c4055363642745   
4      1000000000000000000  0x849ed8601451dcac8012425ccd56fd1339db498c   

                                    subgraphId  \
0  ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
1  ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
2  ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
3  ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
4  ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   

                                subgraphDeploymentID  subgraphversion  \
0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   
1  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   
2  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   
3  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   
4  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   

   subgraphname  
0  PoolTogether  
1  PoolTogether  
2  PoolTogether  
3  PoolTogether  
4  PoolTogether

In [51]:
#get allocationCreated event
url = 'https://api.thegraph.com/subgraphs/name/graphprotocol/graph-network-mainnet'

name_burn_query = '''query{
  nameSignalTransactions(){
    id
    blockNumber
    signer{
      curator{
        id
      }
    }
    type
    nameSignal
    versionSignal
    tokens
    subgraph{
      id
      currentVersion
      {
        version
        subgraphDeployment {
          id
        }
      }
      displayName
    }
  }
}
'''

field_name = 'nameSignalTransactions'
trans_type = 'BurnNSignal'

name_burn_df = query_theGraph(name_burn_query, field_name, url, trans_type, False)

In [52]:
name_burn_df.head()

id  blockNumber  \
0  0xf5fd904385312b521779beb91a757a403132ebf7bbf7...     11486499   
1  0x7b0d39ca37ba86fd5e6ecc4433513ffba4b853a90bd2...     11491383   
2  0xe46b8054c269f1c5811dc5cdd0d4564bb92f370477df...     11491393   
3  0x620c0af5345f21ec87c9b73864d3709d735fb7aac155...     11531871   
4  0x10afff8568c6e870a7b596787cb284e43842892e3a74...     12318426   

                                              signer         type  \
0  {'curator': {'id': '0xb6916933aa0bac4b6d092607...  BurnNSignal   
1  {'curator': {'id': '0x0f3cf18b37c55f5a319d6cae...  BurnNSignal   
2  {'curator': {'id': '0x0f3cf18b37c55f5a319d6cae...  BurnNSignal   
3  {'curator': {'id': '0x849ed8601451dcac8012425c...  BurnNSignal   
4  {'curator': {'id': '0x673b6e9fe607f6ddf4a4f25b...  BurnNSignal   

             nameSignal         versionSignal                   tokens  \
0  89477475325111327822  89477475325111327822  80557400454965249175496   
1                    95                    95                    77029   
2  95000000000000000000  95000000000000000000  68004020455437308993046   
3      1568268903568881      1568268903568881       975006929934390676   
4   1000000000000000000   1000000000000000000    545931348525571351761   

                                            subgraph  
0  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  
1  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  
2  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  
3  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  
4  {'id': '9a8QGQHhrXwuR8mxi4tZGwUkpSacBdzZokNWMj...

In [53]:
name_burn_df['curatorId'] = [i['curator']['id'] for i in name_burn_df['signer']]
name_burn_df['subgraphId'] = [i['id'] for i in name_burn_df['subgraph']]
name_burn_df['subgraphDeploymentID'] = [i['currentVersion']['subgraphDeployment']['id'] for i in name_burn_df['subgraph']]
name_burn_df['subgraphversion'] = [i['currentVersion']['version'] for i in name_burn_df['subgraph']]
name_burn_df['subgraphname'] = [i['displayName'] for i in name_burn_df['subgraph']]
name_burn_df.drop(['signer','subgraph'], axis = 1, inplace = True)
name_burn_df.head()

id  blockNumber  \
0  0xf5fd904385312b521779beb91a757a403132ebf7bbf7...     11486499   
1  0x7b0d39ca37ba86fd5e6ecc4433513ffba4b853a90bd2...     11491383   
2  0xe46b8054c269f1c5811dc5cdd0d4564bb92f370477df...     11491393   
3  0x620c0af5345f21ec87c9b73864d3709d735fb7aac155...     11531871   
4  0x10afff8568c6e870a7b596787cb284e43842892e3a74...     12318426   

          type            nameSignal         versionSignal  \
0  BurnNSignal  89477475325111327822  89477475325111327822   
1  BurnNSignal                    95                    95   
2  BurnNSignal  95000000000000000000  95000000000000000000   
3  BurnNSignal      1568268903568881      1568268903568881   
4  BurnNSignal   1000000000000000000   1000000000000000000   

                    tokens                                   curatorId  \
0  80557400454965249175496  0xb6916933aa0bac4b6d09260719c4055363642745   
1                    77029  0x0f3cf18b37c55f5a319d6cae8d8ba114cb094af0   
2  68004020455437308993046  0x0f3cf18b37c55f5a319d6cae8d8ba114cb094af0   
3       975006929934390676  0x849ed8601451dcac8012425ccd56fd1339db498c   
4    545931348525571351761  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e   

                                     subgraphId  \
0   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
1   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
2   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
3   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
4  9a8QGQHhrXwuR8mxi4tZGwUkpSacBdzZokNWMj2Tvdow   

                                subgraphDeploymentID  subgraphversion  \
0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   
1  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   
2  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   
3  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...                0   
4  0xbbde25a2c85f55b53b7698b9476610c3d1202d88870e...                0   

   subgraphname  
0  PoolTogether  
1  PoolTogether  
2  PoolTogether  
3  PoolTogether  
4  PoolTogether

In [55]:
indexer_name_curation_df = name_mint_df[name_mint_df['subgraphDeploymentID'].isin(unique_subgraphs)].append(name_burn_df[name_burn_df['subgraphDeploymentID'].isin(unique_subgraphs)])

In [56]:
single_indexer_name_df = indexer_df.append(indexer_name_curation_df)
single_indexer_name_df.sort_values(by='blockNumber')
single_indexer_name_df.reset_index(inplace = True)
single_indexer_name_df.head()

index allocationID  blockNumber  epoch  \
0      0          NaN     11474009    NaN   
1      1          NaN     11474009    NaN   
2      2          NaN     11474307    NaN   
3      3          NaN     11474332    NaN   
4      4          NaN     11474426    NaN   

                                                  id  \
0  0xcb621a8a549e4e3c616a7a1e27dc92b28722c90ac37f...   
1  0xcb621a8a549e4e3c616a7a1e27dc92b28722c90ac37f...   
2  0x938641c2dbfd4562c7ab8c60ca98f11394d161ead6b9...   
3  0x67278b0af539dff48945b3a430ada90de00526aed433...   
4  0x19cf8bd30df43cc8518c16bfce7297c32495bbc3c4c1...   

                                      indexer  logIndex subgraphDeploymentID  \
0  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e     121.0                  NaN   
1  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e     122.0                  NaN   
2  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e      17.0                  NaN   
3  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e      38.0                  NaN   
4  0x7ab4cf25330ed7277ac7ab59380b68eea68abb0e     162.0                  NaN   

                      tokens                          type  ...  \
0                        NaN  delegationParametersUpdateds  ...   
1  9615385000000000000000000               stakeDepositeds  ...   
2   165851137200000000000000               stakeDelegateds  ...   
3   251819644650000000000000               stakeDelegateds  ...   
4                        NaN  delegationParametersUpdateds  ...   

  indexingRewardCut queryFeeCut delegationFees amount nameSignal  \
0         1000000.0   1000000.0            NaN    NaN        NaN   
1               NaN         NaN            NaN    NaN        NaN   
2               NaN         NaN            NaN    NaN        NaN   
3               NaN         NaN            NaN    NaN        NaN   
4           90000.0     80000.0            NaN    NaN        NaN   

  versionSignal curatorId  subgraphId  subgraphversion  subgraphname  
0           NaN       NaN         NaN              NaN           NaN  
1           NaN       NaN         NaN              NaN           NaN  
2           NaN       NaN         NaN              NaN           NaN  
3           NaN       NaN         NaN              NaN           NaN  
4           NaN       NaN         NaN              NaN           NaN  

[5 rows x 29 columns]

In [57]:
# save all events for the indexer
single_indexer_name_df.to_csv('../another_indexer/single_indexer/singleIndexername.csv', index = False, header = True)

In [63]:
# function used to query each type of event from The Graph
def query_theGraph_subgraph(raw_query, field_name, url, trans_type, verbose=False):

    query_parts =raw_query.split(')')
    paginator = ", where: {}" 
    n = 0
    records = []
    while n < 1000:
        if (n == 0):
            # order by blockNumber to get all events, as deafult ordering is by id
            query = 'query '+query_parts[0] + 'orderBy:createdAt, where:{createdAt_gt: 0})' + query_parts[1]
        else:
            query = 'query '+query_parts[0]+ 'orderBy:createdAt, where: {createdAt_gt: ' + str(indexer) + '})'+query_parts[1]

        if verbose:
            print(query)

        r = requests.post(url, json = {'query':query})

        try:
            d = json.loads(r.content)['data'][field_name]
        except:
            print(r.content)
            errors = json.loads(r.content)['errors']
            print(errors)
            for e in errors:
                print(e['message'])

        #print(f'results {len(d)}')
        records.extend(d)
        #print(f'total {len(records)}')
        try:
            indexer = d[-1]['createdAt']
        except:
            print('noblock')
        
        n += 1
        if len(d) < 99:
            break
        
    return pd.DataFrame(records)

In [64]:
#get allocationCreated event
url = 'https://api.thegraph.com/subgraphs/name/graphprotocol/graph-network-mainnet'

subgraph_query = '''query{
	subgraphs(){
    id
    owner{
      id
    }
    currentVersion{
      id
      subgraphDeployment{
        id
      }
      version
    }
    createdAt
    updatedAt
    active
    migrated
    displayName
  }
}
'''

field_name = 'subgraphs'
trans_type = 'BurnNSignal'

subgraph_df = query_theGraph_subgraph(subgraph_query, field_name, url, trans_type, False)

In [65]:
subgraph_df.head()

id  \
0  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0   
1   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN   
2  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-0   
3  Gv1rewdMuEeDQ9sWsWMjJfwKWrTxo5e19vgxr1br7Ut4   
4  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-1   

                                               owner  \
0  {'id': '0x93606b27cb5e4c780883ec4f6b7bed5f6572...   
1  {'id': '0x93606b27cb5e4c780883ec4f6b7bed5f6572...   
2  {'id': '0x673b6e9fe607f6ddf4a4f25b386b846c5c82...   
3  {'id': '0x673b6e9fe607f6ddf4a4f25b386b846c5c82...   
4  {'id': '0x673b6e9fe607f6ddf4a4f25b386b846c5c82...   

                                      currentVersion   createdAt   updatedAt  \
0  {'id': '0x93606b27cb5e4c780883ec4f6b7bed5f6572...  1608252009  1645807948   
1  {'id': 'ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasU...  1608252009  1645807948   
2  {'id': '0x673b6e9fe607f6ddf4a4f25b386b846c5c82...  1619441050  1619790992   
3  {'id': 'Gv1rewdMuEeDQ9sWsWMjJfwKWrTxo5e19vgxr1...  1619441050  1619790992   
4  {'id': '0x673b6e9fe607f6ddf4a4f25b386b846c5c82...  1619442230  1645807948   

   active  migrated   displayName  
0   False      True  PoolTogether  
1   False      True  PoolTogether  
2   False     False  PoolTogether  
3   False     False  PoolTogether  
4   False      True  PoolTogether

In [66]:
subgraph_df['ownerId'] = [i['id'] for i in subgraph_df['owner']]
subgraph_df['version'] = [i['version'] for i in subgraph_df['currentVersion']]
subgraph_df['subgraphDeploymentId'] = [i['subgraphDeployment']['id'] for i in subgraph_df['currentVersion']]
subgraph_df['subgraphid'] = [i['id'] for i in subgraph_df['currentVersion']]
subgraph_df.drop(['owner', 'currentVersion'], axis = 1, inplace = True)
subgraph_df.head()

id   createdAt   updatedAt  \
0  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0  1608252009  1645807948   
1   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN  1608252009  1645807948   
2  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-0  1619441050  1619790992   
3  Gv1rewdMuEeDQ9sWsWMjJfwKWrTxo5e19vgxr1br7Ut4  1619441050  1619790992   
4  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-1  1619442230  1645807948   

   active  migrated   displayName                                     ownerId  \
0   False      True  PoolTogether  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd   
1   False      True  PoolTogether  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd   
2   False     False  PoolTogether  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e   
3   False     False  PoolTogether  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e   
4   False      True  PoolTogether  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e   

   version                               subgraphDeploymentId  \
0        0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...   
1        0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...   
2        0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...   
3        0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...   
4        0  0xbbde25a2c85f55b53b7698b9476610c3d1202d88870e...   

                                       subgraphid  
0  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0-0  
1   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN-0  
2  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-0-0  
3  Gv1rewdMuEeDQ9sWsWMjJfwKWrTxo5e19vgxr1br7Ut4-0  
4  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-1-0

In [68]:
subgraph_df[10:20]

id   createdAt   updatedAt  \
10  0x9efbea665b79f366fcbb390a55c617257e0c678c-0  1619553667  1645638939   
11  D4kczV9c2KTC5GArH2M54gs5mGZaigBpsiR7rCwgHqBX  1619553667  1645638939   
12  0x26cf67040678eb0f5654c9cbaad78dc1694cbafa-0  1619557989  1645639205   
13  HTmE4KFztgBCbs2fdM7ai3jV32nufPs4xqXqfnLU3WRU  1619557989  1645639205   
14  0x0a0319671f2d3c18fb55ab555b48bc01f27747a4-0  1619558619  1645639205   
15  41LCrgtCNBQyDiVVyZEuPxbvkBH9BxxLU3nEZst77V8o  1619558619  1645639205   
16  0xfc3ac80003d8a5181e554d03983284e4341a7610-0  1619560579  1645639205   
17  3SJSsXJkTkkDiRT2X3uWFcKaAnvWScLhL3YVL1oFimuF  1619560579  1645639205   
18  0xd6ce4c87ec3fb6e80d87ff5fa7c5ec8fdefadf5c-0  1619561533  1647824645   
19  GxV9XL6Wnjz75z919NPNdrLhEkqDR99PweUY3oh7Lh94  1619561533  1647824645   

    active  migrated         displayName  \
10    True      True         RAI Mainnet   
11    True      True         RAI Mainnet   
12    True      True    mStable Protocol   
13    True      True    mStable Protocol   
14    True      True  UMA Mainnet Voting   
15    True      True  UMA Mainnet Voting   
16    True      True  Opyn Gamma Mainnet   
17    True      True  Opyn Gamma Mainnet   
18    True      True           DODOEX V2   
19    True      True           DODOEX V2   

                                       ownerId  version  \
10  0x9efbea665b79f366fcbb390a55c617257e0c678c        2   
11  0x9efbea665b79f366fcbb390a55c617257e0c678c        2   
12  0x26cf67040678eb0f5654c9cbaad78dc1694cbafa        0   
13  0x26cf67040678eb0f5654c9cbaad78dc1694cbafa        0   
14  0x0a0319671f2d3c18fb55ab555b48bc01f27747a4        0   
15  0x0a0319671f2d3c18fb55ab555b48bc01f27747a4        0   
16  0xfc3ac80003d8a5181e554d03983284e4341a7610        0   
17  0xfc3ac80003d8a5181e554d03983284e4341a7610        0   
18  0xd6ce4c87ec3fb6e80d87ff5fa7c5ec8fdefadf5c        2   
19  0xd6ce4c87ec3fb6e80d87ff5fa7c5ec8fdefadf5c        2   

                                 subgraphDeploymentId  \
10  0x5b83184ead3290c43e0a5524f086595e3ced90af300f...   
11  0x5b83184ead3290c43e0a5524f086595e3ced90af300f...   
12  0xa7d9d3a173d3d62ce3d05c2d29f3447b04edc248cbcf...   
13  0xa7d9d3a173d3d62ce3d05c2d29f3447b04edc248cbcf...   
14  0x2aaeb45afa62af1cc8f6d61decd5249429e0aaed6799...   
15  0x2aaeb45afa62af1cc8f6d61decd5249429e0aaed6799...   
16  0x014e8a3184d5fad198123419a7b54d5f7c9f8a981116...   
17  0x014e8a3184d5fad198123419a7b54d5f7c9f8a981116...   
18  0x969f6c63e40c58d6836ce6afb2b71417e34c86e50bac...   
19  0x969f6c63e40c58d6836ce6afb2b71417e34c86e50bac...   

                                        subgraphid  
10  0x9efbea665b79f366fcbb390a55c617257e0c678c-0-2  
11  D4kczV9c2KTC5GArH2M54gs5mGZaigBpsiR7rCwgHqBX-2  
12  0x26cf67040678eb0f5654c9cbaad78dc1694cbafa-0-0  
13  HTmE4KFztgBCbs2fdM7ai3jV32nufPs4xqXqfnLU3WRU-0  
14  0x0a0319671f2d3c18fb55ab555b48bc01f27747a4-0-0  
15  41LCrgtCNBQyDiVVyZEuPxbvkBH9BxxLU3nEZst77V8o-0  
16  0xfc3ac80003d8a5181e554d03983284e4341a7610-0-0  
17  3SJSsXJkTkkDiRT2X3uWFcKaAnvWScLhL3YVL1oFimuF-0  
18  0xd6ce4c87ec3fb6e80d87ff5fa7c5ec8fdefadf5c-0-2  
19  GxV9XL6Wnjz75z919NPNdrLhEkqDR99PweUY3oh7Lh94-2

In [89]:
subgraph_df['subgraph_version'] = [i.split('-')[0]+'-'+i.split('-')[1] for i in  subgraph_df['subgraphid']]
subgraph_df.head()

id   createdAt   updatedAt  \
0  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0  1608252009  1645807948   
1   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN  1608252009  1645807948   
2  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-0  1619441050  1619790992   
3  Gv1rewdMuEeDQ9sWsWMjJfwKWrTxo5e19vgxr1br7Ut4  1619441050  1619790992   
4  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-1  1619442230  1645807948   

   active  migrated   displayName                                     ownerId  \
0   False      True  PoolTogether  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd   
1   False      True  PoolTogether  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd   
2   False     False  PoolTogether  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e   
3   False     False  PoolTogether  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e   
4   False      True  PoolTogether  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e   

   version                               subgraphDeploymentId  \
0        0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...   
1        0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...   
2        0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...   
3        0  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...   
4        0  0xbbde25a2c85f55b53b7698b9476610c3d1202d88870e...   

                                       subgraphid  \
0  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0-0   
1   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN-0   
2  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-0-0   
3  Gv1rewdMuEeDQ9sWsWMjJfwKWrTxo5e19vgxr1br7Ut4-0   
4  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-1-0   

                                 subgraph_version  
0    0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0  
1   ziL9z9yVvVoksZ5MhyQFNjtspRdxMNDvwtYasUtXCvN-0  
2    0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-0  
3  Gv1rewdMuEeDQ9sWsWMjJfwKWrTxo5e19vgxr1br7Ut4-0  
4    0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-1

In [69]:
# function used to query each type of event from The Graph
def query_theGraph_events(raw_query, field_name, url, trans_type, verbose=False):

    query_parts =raw_query.split(')')
    paginator = ", where: {}" 
    n = 0
    records = []
    while n < 1000:
        if (n == 0):
            # order by blockNumber to get all events, as deafult ordering is by id
            query = 'query '+query_parts[0] + 'orderBy:blockNumber, where:{blockNumber_gt: 0})' + query_parts[1]
        else:
            query = 'query '+query_parts[0]+ 'orderBy:blockNumber, where: {blockNumber_gt: ' + str(indexer) + '})'+query_parts[1]

        if verbose:
            print(query)

        r = requests.post(url, json = {'query':query})

        try:
            d = json.loads(r.content)['data'][field_name]
        except:
            print(r.content)
            errors = json.loads(r.content)['errors']
            print(errors)
            for e in errors:
                print(e['message'])

        #print(f'results {len(d)}')
        records.extend(d)
        #print(f'total {len(records)}')
        try:
            indexer = d[-1]['createdAt']
        except:
            print('noblock')
        
        n += 1
        if len(d) < 99:
            break
        
    return pd.DataFrame(records)

In [71]:
#get allocationCreated event
url = 'https://api.thegraph.com/subgraphs/name/fordn/graph-network-events'

withdraw_query = '''query{
	grtwithdrawns(){
        id
        blockNumber
        graphAccount
        subgraphNumber
        nameCurator
        nSignalBurnt
        withdrawnGRT
  }
}
'''

field_name = 'grtwithdrawns'

withdraw_df = query_theGraph_events(withdraw_query, field_name, url, trans_type, False)

noblock


In [73]:
withdraw_df.head()

id blockNumber  \
0  0x6b79238a65b76c0c34c3c1d80baf336d2d8825a56dca...    12323378   
1  0x949a0846530d16ab2d7752a835e35e4ad3dea65795af...    12342271   
2  0x43ca80f165479c0c3e845a99c0cf607a762158c96d87...    12788295   
3  0xbd3708e37001acedcab6e329a37401920daff88caedd...    12788326   
4  0xa2f3f0f3ed3084b57e8cfbf3a2e156f000657974c9db...    12788408   

                                 graphAccount subgraphNumber  \
0  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e              3   
1  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e              0   
2  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   
3  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   
4  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   

                                  nameCurator           nSignalBurnt  \
0  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e    3122498999199199102   
1  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e     147529798656557600   
2  0xc6ba3e757f3af487e388230f1e3a40615ea24002  221040135439528302402   
3  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd  279284800875378823397   
4  0xc18d03a8be67cb08c01434861dc561a70c4b3aa8      64571405224668812   

               withdrawnGRT  
0       9750000000000000000  
1     305378117070384881711  
2  117649984549175437607963  
3  148651069374670374373841  
4      34368531361487313663

In [86]:
for i, j in enumerate(withdraw_df.iteritems()):
    print(j)

('id', 0     0x6b79238a65b76c0c34c3c1d80baf336d2d8825a56dca...
1     0x949a0846530d16ab2d7752a835e35e4ad3dea65795af...
2     0x43ca80f165479c0c3e845a99c0cf607a762158c96d87...
3     0xbd3708e37001acedcab6e329a37401920daff88caedd...
4     0xa2f3f0f3ed3084b57e8cfbf3a2e156f000657974c9db...
5     0x4439e492fb6f303b3b78760c2fc8452595aa9cc8aa10...
6     0x4264cb79c347b5f270f32e8c97422bfb6b48746702ba...
7     0xd19e9fab97ded5f28731755d238c6c9018b8a7ac5b00...
8     0x8ca822e4bd7da1d9f25dca668209c2dcdc15f58e653b...
9     0x145dc839a4cc2347c3fb1e99b8df1bccb8f1c3a8f89c...
10    0xd92fd32c928f8c7fea7f3988b23c7bd0a41fd8e994db...
11    0xaee46e089e752e9309c8e41326a6ef3dd7971355679a...
12    0xba51a456626419751dcc6cc9d9daa6514439cde74ad2...
13    0x6e4663ab8d07c99caa82830c71e3b7b3ed03b5678c75...
14    0x70e6810333c724256aab4a27307959959d74bc0771f6...
15    0x76e4985ba4b2a1b430fce960a073a94dff39cb139edd...
16    0xd2fe8c1401f93dae83844ae26c849376c9a20b146aab...
17    0xa001c34d7d05e168fa81a5670aa01db96

In [88]:
withdraw_df['subgraph_w_version'] = withdraw_df['graphAccount']+'-'+withdraw_df['subgraphNumber']
withdraw_df.head()

id blockNumber  \
0  0x6b79238a65b76c0c34c3c1d80baf336d2d8825a56dca...    12323378   
1  0x949a0846530d16ab2d7752a835e35e4ad3dea65795af...    12342271   
2  0x43ca80f165479c0c3e845a99c0cf607a762158c96d87...    12788295   
3  0xbd3708e37001acedcab6e329a37401920daff88caedd...    12788326   
4  0xa2f3f0f3ed3084b57e8cfbf3a2e156f000657974c9db...    12788408   

                                 graphAccount subgraphNumber  \
0  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e              3   
1  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e              0   
2  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   
3  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   
4  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   

                                  nameCurator           nSignalBurnt  \
0  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e    3122498999199199102   
1  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e     147529798656557600   
2  0xc6ba3e757f3af487e388230f1e3a40615ea24002  221040135439528302402   
3  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd  279284800875378823397   
4  0xc18d03a8be67cb08c01434861dc561a70c4b3aa8      64571405224668812   

               withdrawnGRT                            subgraph_w_version  
0       9750000000000000000  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-3  
1     305378117070384881711  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-0  
2  117649984549175437607963  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0  
3  148651069374670374373841  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0  
4      34368531361487313663  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0

In [97]:
withdraw_df['subgraphDeploymentId'] = 0

In [98]:
for i, j in enumerate(withdraw_df['subgraph_w_version']):
    for k, l in enumerate(subgraph_df['subgraph_version']):
        if j in l:
            withdraw_df['subgraphDeploymentId'][i] = subgraph_df.iloc[k]['subgraphDeploymentId']
withdraw_df.head()

/tmp/ipykernel_2593911/3906413835.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  withdraw_df['subgraphDeploymentId'][i] = subgraph_df.iloc[k]['subgraphDeploymentId']
/home/jesse/anaconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


id blockNumber  \
0  0x6b79238a65b76c0c34c3c1d80baf336d2d8825a56dca...    12323378   
1  0x949a0846530d16ab2d7752a835e35e4ad3dea65795af...    12342271   
2  0x43ca80f165479c0c3e845a99c0cf607a762158c96d87...    12788295   
3  0xbd3708e37001acedcab6e329a37401920daff88caedd...    12788326   
4  0xa2f3f0f3ed3084b57e8cfbf3a2e156f000657974c9db...    12788408   

                                 graphAccount subgraphNumber  \
0  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e              3   
1  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e              0   
2  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   
3  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   
4  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd              0   

                                  nameCurator           nSignalBurnt  \
0  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e    3122498999199199102   
1  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e     147529798656557600   
2  0xc6ba3e757f3af487e388230f1e3a40615ea24002  221040135439528302402   
3  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd  279284800875378823397   
4  0xc18d03a8be67cb08c01434861dc561a70c4b3aa8      64571405224668812   

               withdrawnGRT                            subgraph_w_version  \
0       9750000000000000000  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-3   
1     305378117070384881711  0x673b6e9fe607f6ddf4a4f25b386b846c5c82995e-0   
2  117649984549175437607963  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0   
3  148651069374670374373841  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0   
4      34368531361487313663  0x93606b27cb5e4c780883ec4f6b7bed5f6572d1dd-0   

                                subgraphDeploymentId  
0  0xbae01a063ad846d7e4200757480544b5feb1f0217d94...  
1  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
2  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
3  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...  
4  0x31edcacc9a53bc8ab4be2eeb0d873409da4c4228cb2d...